## add api settings

In [1]:
api_key= 'PKMEHDXWVCBV5PIGRR1V'
api_key_secret= '2xS2lzB2Is5yV80doyuqMJZvDi8x5ii9dnDYg1zd'

## import libraries

In [2]:
import requests
import pandas as pd
from IPython.display import HTML
import json
from time import sleep
from datetime import datetime
import os


## get symbols and symbols name to classification

In [3]:
import requests

url = "https://paper-api.alpaca.markets/v2/assets"

headers = {
    "accept": "application/json",
    "APCA-API-KEY-ID": api_key,
    "APCA-API-SECRET-KEY": api_key_secret
}

params = {
    "status": "active"
}

response = requests.get(url, headers=headers, params=params)

print(response.text)

[{"id":"0f8f4052-82b6-4a6c-ad60-483c17b82e35","cusip":null,"class":"us_equity","exchange":"OTC","symbol":"MCLDF","name":"MCLOUD TECHNOLOGIES CORP Common Shares","status":"active","tradable":false,"marginable":false,"maintenance_margin_requirement":100,"margin_requirement_long":"100","margin_requirement_short":"100","shortable":false,"easy_to_borrow":false,"fractionable":false,"attributes":[]},{"id":"7f82dad7-a655-475e-866a-21110b263e9f","cusip":null,"class":"us_equity","exchange":"NASDAQ","symbol":"MSSWF","name":"METAL SKY STAR ACQUISITION CORP Warrant   2029-03-31","status":"active","tradable":false,"marginable":false,"maintenance_margin_requirement":100,"margin_requirement_long":"100","margin_requirement_short":"100","shortable":false,"easy_to_borrow":false,"fractionable":false,"attributes":[]},{"id":"b6c5d64c-a2f3-44ff-b96a-b20aa1255d34","cusip":null,"class":"us_equity","exchange":"OTC","symbol":"DTCB","name":"Solo Brands, Inc.","status":"active","tradable":false,"marginable":false,

In [4]:
df_symbol = pd.DataFrame(json.loads(response.text))
df_symbol

id cusip      class exchange  \
0      0f8f4052-82b6-4a6c-ad60-483c17b82e35  None  us_equity      OTC   
1      7f82dad7-a655-475e-866a-21110b263e9f  None  us_equity   NASDAQ   
2      b6c5d64c-a2f3-44ff-b96a-b20aa1255d34  None  us_equity      OTC   
3      0abc2677-755e-467f-b23c-263748444774  None  us_equity      OTC   
4      f8974a61-2f69-4362-9913-09f9810816b1  None  us_equity      OTC   
...                                     ...   ...        ...      ...   
12391  684a2cad-85c3-4e09-ac9d-b8893dd1e02f  None     crypto   CRYPTO   
12392  85cbcac6-e08c-4516-a635-ebbd6515ccd3  None     crypto   CRYPTO   
12393  7b4c3c70-b54b-4328-85fb-c24bdb45ef45  None     crypto   CRYPTO   
12394  764fb9f4-14a1-4c93-bcf9-6a460029143d  None     crypto   CRYPTO   
12395  ec294909-7421-4bcd-b991-e8de5a67ecab  None     crypto   CRYPTO   

          symbol                                               name  status  \
0          MCLDF             MCLOUD TECHNOLOGIES CORP Common Shares  active   
1          MSSWF  METAL SKY STAR ACQUISITION CORP Warrant   2029...  active   
2           DTCB                                  Solo Brands, Inc.  active   
3          ISUNQ                                       ISUN INC COM  active   
4          RADCQ                        RITE AID CORP COM PAR $1.00  active   
...          ...                                                ...     ...   
12391  USDT/USDC                              USD Tether / USD Coin  active   
12392    XRP/USD                                 Ripple / US Dollar  active   
12393  DOGE/USDT                              Dogecoin / USD Tether  active   
12394    DOT/USD                               Polkadot / US Dollar  active   
12395   DOT/USDC                                Polkadot / USD Coin  active   

       tradable  marginable  maintenance_margin_requirement  \
0         False       False                             100   
1         False       False                             100   
2         False       False                             100   
3         False       False                             100   
4         False       False                             100   
...         ...         ...                             ...   
12391      True       False                             100   
12392      True       False                             100   
12393      True       False                             100   
12394      True       False                             100   
12395      True       False                             100   

      margin_requirement_long margin_requirement_short  shortable  \
0                         100                      100      False   
1                         100                      100      False   
2                         100                      100      False   
3                         100                      100      False   
4                         100                      100      False   
...                       ...                      ...        ...   
12391                     100                      100      False   
12392                     100                      100      False   
12393                     100                      100      False   
12394                     100                      100      False   
12395                     100                      100      False   

       easy_to_borrow  fractionable                            attributes  \
0               False         False                                    []   
1               False         False                                    []   
2               False          True  [fractional_eh_enabled, has_options]   
3               False         False                         [has_options]   
4               False         False                         [has_options]   
...               ...           ...                                   ...   
12391           False          True                                    []   
12392        

In [6]:
df_symbol[['symbol', 'name']].to_csv('assets.csv')

## I added the dataset to be classified by chat gpt o3 following the rule for 
Prompt: Crie uma tabela com os ativos selecionados que podem impactar o xau/usd, então deve conter o símbolo, nome e grau de impacto no xau/usd
Salvei o resultado em assets - assets_with_impact.csv

In [5]:
url = "https://data.alpaca.markets/v1beta1/news"
assets_target = pd.read_csv('assets - assets_with_impact.csv')
symbols = ','.join(asset["Símbolo"] for _, asset in assets_target.iterrows())

start_date_global = datetime(2020,1,1)
end_date_global = datetime(2025,6,6)
year_month_start = list()
for year_month in pd.date_range(start=start_date_global, end=end_date_global, freq='MS'):
  year_month_start.append(year_month.date())


In [6]:
def fetch_data(next_page_token, start_date, end_date, df_news_concat):
  headers = {
      "accept": "application/json",
      "APCA-API-KEY-ID": api_key,
      "APCA-API-SECRET-KEY": api_key_secret,
  }
  params= {
      "symbols":symbols,
      "start":str(start_date),
      "end":str(end_date),
      "include_content": True,
      "limit":"50",
      "page_token":next_page_token
  }
  data_actual = requests.get(url, headers=headers, params= params, json=True).json()

  str_next_page_token = data_actual['next_page_token']
  df_news_actual = pd.DataFrame(data_actual['news'])

  df_news_concat = pd.concat([df_news_actual, df_news_concat], axis=0, ignore_index=True)
  next_page_token = str_next_page_token
  return df_news_concat, next_page_token


In [8]:
os.makedirs('raw/news')
for year_month in year_month_start:
  next_page_token=''
  start_date = year_month
  end_date = (year_month+ pd.offsets.MonthEnd(0)).date() \
    if (year_month+ pd.offsets.MonthEnd(0)).date()< end_date_global.date() else end_date_global.date()
  df_news_concat = pd.DataFrame()
  
  while True:
    if next_page_token == None:
      break
    else:
      df_news_concat, next_page_token = fetch_data(next_page_token, start_date, end_date, df_news_concat)
  df_news_concat.to_csv(f'raw/news/dt={start_date}.csv')
  sleep(30)


In [36]:
##for article in df_news_concat.content.head(9).to_list():
##  display(HTML(article))

In [38]:
df = pd.read_csv('news/dt=2020-01-01.csv')

In [39]:
df

Unnamed: 0             author  \
0            0         Lisa Levin   
1            1         Lisa Levin   
2            2         Lisa Levin   
3            3  Benzinga Newsdesk   
4            4       Wayne Duggan   
5            5  Benzinga Newsdesk   
6            6      ETF Professor   
7            7     Tanzeel Akhtar   
8            8       Wayne Duggan   
9            9  Benzinga Newsdesk   
10          10  Benzinga Newsdesk   

                                              content            created_at  \
0   <p>During Thursday&#39;s morning trading, 142 ...  2020-01-30T15:25:31Z   
1   <p>Monday&#39;s morning session saw 100 compan...  2020-01-27T15:33:00Z   
2   <p>Before 10 a.m. ET Friday, 350 stocks made n...  2020-01-24T15:41:55Z   
3                                                 NaN  2020-01-24T12:12:05Z   
4   <p>Illiquidity in the U.S. repo market spooked...  2020-01-14T20:23:56Z   
5                                                 NaN  2020-01-13T18:34:59Z   
6   <p>With a yield of just 0.39%, the <strong>Van...  2020-01-09T20:46:00Z   
7   <p><a href="https://www.benzinga.com/topic/gol...  2020-01-08T20:38:04Z   
8   <p>U.S. Sen. Bernie Sanders may have a real ch...  2020-01-08T15:07:24Z   
9   <p>Benzinga Pro&#39;s Stocks To Watch For Wedn...  2020-01-08T13:50:30Z   
10                                                NaN  2020-01-07T23:26:37Z   

                                             headline        id  \
0           Stocks That Hit 52-Week Highs On Thursday  15218386   
1             Stocks That Hit 52-Week Highs On Monday  15189567   
2             Stocks That Hit 52-Week Highs On Friday  15181171   
3   US Treasury Secretary Steve Mnuchin Says Ultra...  15179207   
4   The Repo Market Is So Broken That The Fed Want...  15122298   
5   UPDATE: B. Riley FBR Upgrades Newmont To Buy, ...  15114484   
6             Gold Miners ETF Becomes A Dividend Idea  15096113   
7   Gold's Santa Claus Rally Followed By Surge On ...  15075199   
8   Gundlach: Bernie Sanders Is The Biggest Market...  15091460   
9   Benzinga Pro's Top 5 Stocks To Watch For Wed.,...  15090880   
10  Gold Up $13/Oz After Hours Amid Reports Of Ong...  15088637   

                                               images  source  summary  \
0                                                  []     NaN      NaN   
1                                                  []     NaN      NaN   
2                                                  []     NaN      NaN   
3                                                  []     NaN      NaN   
4   [{'size': 'large', 'url': 'https://cdn.benzing...     NaN      NaN   
5                                                  []     NaN      NaN   
6   [{'size': 'large', 'url': 'https://cdn.benzing...     NaN      NaN   
7   [{'size': 'large', 'url': 'https://cdn.benzing...     NaN      NaN   
8   [{'size': 'large', 'url': 'https://cdn.benzing...     NaN      NaN   
9                                                  []     NaN      NaN   
10                                                 []     NaN      NaN   

                                              symbols            updated_at  \
0   ['AEE', 'AEP', 'AGR', 'AHCO', 'AJG', 'ALEC', '...  2020-01-30T15:25:32Z   
1   ['ACHN', 'ADSW', 'AEP', 'AHPI', 'ALTKF', 'APT'...  2020-01-27T15:33:00Z   
2   ['AAON', 'AAPL', 'AB', 'ADBE', 'ADGS', 'ADSK',...  2020-01-24T15:41:56Z   
3                                      ['SPY', 'TLT']  2020-01-24T12:12:05Z   
4                              ['GBTC', 'GLD', 'SPY']  2020-01-14T20:23:56Z   
5                                      ['GDX', 'NEM']  2020-01-13T18:34:59Z   
6                               ['AUY', 'GDX', 'NEM']  2020-01-09T20:46:00Z   
7                                      ['GDX', 'GLD']  2020-01-08T20:38:04Z   
8                               ['EEM', 'SPY', 'UUP']  2020-01-08T15:07:25Z   
9   ['BA', 'CVS', 'GDX', 'GLD', 'LK', 'PIXY', 'RAD...  2020-01-08T13:50:31Z   
10                                     ['GDX', 